# Calculate $\omega \text{s}$ and corresponding eigenvectors

In [2]:
from mlat.const import dirac, pauli
import numpy as np
import numpy.linalg as la
import plotly.graph_objects as go

vs = np.arange(0, 1.5, 0.05)
w = 1.
m = 1.
N = 6
A = 0
B = 1

d = dirac(N, 2)
p = pauli()


# H = 0
# for m in range(N):
#     H += v * np.kron(np.dot(inter.ket(m), inter.bra(m)), p.x)
# for m in range(N-1):
#     fst = np.kron(np.dot(inter.ket(m+1), inter.bra(m)), (p.x + 1.j * p.y) / 2)
#     H += w * (fst + fst.T.conj())

Es = []
for v in vs:
    H = 0
    for m in range(N):
        fst = np.kron(d.ket(m, B), d.bra(m, A))
        H += v * (fst + fst.conj().T)
    for m in range(N-1):
        fst = np.kron(d.ket(m+1, A), d.bra(m, B))
        H += w * (fst + fst.T.conj())

    M = np.diag([m] * (N*2))

    evals, evecs = la.eig(la.inv(M).dot(H))
    idcs = np.argsort(evals)
    evals, evecs = evals[idcs], evecs[idcs]
    E = evals.real
    ws = np.sqrt(np.abs(evals.real))
    Es.append(E)
Es = np.array(Es)
print(Es[0])
# Create traces
fig = go.Figure()
for i in range(N*2):
    fig.add_trace(go.Scatter(x=vs, y=Es[:, i], mode='lines', name=f"E{i}"))

fig.show()

[-0.25 -0.25 -0.25 -0.25 -0.25  0.    0.    0.25  0.25  0.25  0.25  0.25]


In [2]:
from mlat.const import dirac, pauli
import numpy as np
import numpy.linalg as la


v = 0.3
w = 1.
m = 1.
N = 10
A = 0
B = 1

d = dirac(N, 2)
p = pauli()


# H = 0
# for m in range(N):
#     H += v * np.kron(np.dot(inter.ket(m), inter.bra(m)), p.x)
# for m in range(N-1):
#     fst = np.kron(np.dot(inter.ket(m+1), inter.bra(m)), (p.x + 1.j * p.y) / 2)
#     H += w * (fst + fst.T.conj())


H = 0
for m in range(1, N-1):
    fst = np.kron(d.ket(m, B), d.bra(m, A))
    H += v * (fst + fst.conj().T)
for m in range(1, N-2):
    fst = np.kron(d.ket(m+1, A), d.bra(m, B))
    H += w * (fst + fst.T.conj())
# Fixed points
H += w * np.kron(d.ket(0, B), d.bra(1, A))
H += w * np.kron(d.ket(N-1, A), d.bra(N-2, B))

M = np.diag([m] * (N * 2))

evals, evecs = la.eig(la.inv(M).dot(H))
idcs = np.argsort(evals)
evals, evecs = evals[idcs], evecs[idcs]
E = evals.real
ws = np.sqrt(np.abs(evals.real))
print(E)
print(ws)

[-1.83325174e-01 -1.76307494e-01 -1.65126070e-01 -1.50619153e-01
 -1.34136372e-01 -1.17823395e-01 -1.05028098e-01 -8.52930026e-06
  0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
  8.52930026e-06  1.05028098e-01  1.17823395e-01  1.34136372e-01
  1.50619153e-01  1.65126070e-01  1.76307494e-01  1.83325174e-01]
[0.42816489 0.41988986 0.40635707 0.38809683 0.36624633 0.34325413
 0.32408039 0.0029205  0.         0.         0.         0.
 0.0029205  0.32408039 0.34325413 0.36624633 0.38809683 0.40635707
 0.41988986 0.42816489]


# Animation

In [3]:
import numpy as np
import plotly.graph_objects as go

# Parameters
mode = -1

w = ws[mode] # /s

# Print infos
print("Angular frequency: ", w)

# Parameters for animation
fps = 30 # /s
animation_length = 100 # s

x = np.array([2 * i for i in range((N-2) * 2)])
y = np.array([0.] * ((N-2) * 2))

# Construct frames
frames = []
for t in range(int(animation_length * fps)):
    dt = t / fps
    dphase = np.exp(1.j * dt * w * 2 * np.pi)
    dy = []
    for m in range(1, N-1):
        dy.append(evecs[mode].dot(d.ket(m, A))[0] * dphase)
        dy.append(evecs[mode].dot(d.ket(m, B))[0] * dphase)
    dy = np.array(dy)
    frames.append(go.Frame(data=[go.Scatter(x=x,y=y+dy.real, line_shape='spline')]))

# Figure components
start_button = dict(
        label="Play",
        method="animate",
        args=[
            None, 
            {
                "frame":{"duration": 1000 / fps, "redraw": False},
                "fromcurrent": True, 
                "transition": {"duration": 100}
            }])
pause_button = dict(
        label="Pause",
        method="animate",
        args=[
            [None], 
            {
                "frame": {"duration": 0, "redraw": False},
                "mode": "immediate",
                "transition": {"duration": 0}
            }])

# Plot
fig = go.Figure(
    data=frames[0].data,
    layout=go.Layout(
        title="Dispersion relation animation",
        yaxis=dict(range=[-1., 1.], autorange=False),
        updatemenus=[
            dict(
                type="buttons",
                buttons=[start_button, pause_button
            ])
        ]
    ),
    frames=frames[1:])
fig.show()

Angular frequency:  0.42816489149951986
